In [366]:
import requests 
import json
import os
from dotenv import load_dotenv
import pandas as pd
from pandas import json_normalize
import tweepy
import time
load_dotenv()

True

In [367]:
stone = pd.read_excel("../data/musicbrainz.xlsx")

In [368]:
stone.isna().sum()

#            0
Year         0
Title        0
Artist       0
Type         0
Rating      38
Releases     0
Genre        0
dtype: int64

In [369]:
stone.Year.unique()

array([1971, 1966, 1976, 1969, 1991, 1977, 1984, 1975, 1998, 1982, 1967,
       1972, 1988, 1979, 2010, 1965, 2015, 2000, 1994, 1993, 1968, 1959,
       2016, 2006, 1973, 1992, 1980, 1997, 1987, 1986, 2001, 1963, 1996,
       1985, 1995, 2003, 2013, 1970, 1978, 2011, 2012, 1989, 1999, 1974,
       2005, 1962, 1990, 1983, 2017, 1960, 1964, 2007, 2008, 2002, 1957,
       2004, 2018, 1955, 1958, 2019, 1956, 1981, 1961, 2014, 2009])

In [370]:
stone

#  Year                              Title              Artist  \
0      1  1971                    What’s Going On         Marvin Gaye   
1      2  1966                         Pet Sounds      The Beach Boys   
2      3  1971                               Blue       Joni Mitchell   
3      4  1976           Songs in the Key of Life       Stevie Wonder   
4      5  1969                         Abbey Road         The Beatles   
..   ...   ...                                ...                 ...   
495  496  1998         ¿Dónde están los ladrones?             Shakira   
496  497  1985  The Indestructible Beat of Soweto     Various Artists   
497  498  1977                            Suicide             Suicide   
498  499  1977                          Ask Rufus  Rufus & Chaka Khan   
499  500  2004                            Funeral         Arcade Fire   

                    Type  Rating  Releases                     Genre  
0                  Album    4.65        38                       r&b  
1                  Album    4.45        47                      rock  
2                  Album    4.45        18                      folk  
3                  Album    4.55        24                      soul  
4                  Album    4.70        54                      rock  
..                   ...     ...       ...                       ...  
495                Album    4.50         4                       pop  
496  Album + Compilation     NaN         3  mbaqanga , south african  
497                Album    4.00        10                      rock  
498                Album     NaN         2                       r&b  
499                Album    4.65        17              rock , indie  

[500 rows x 8 columns]

In [371]:
stone.rename(columns={"Title": "Album"}, inplace = True)

In [372]:
stone

#  Year                              Album              Artist  \
0      1  1971                    What’s Going On         Marvin Gaye   
1      2  1966                         Pet Sounds      The Beach Boys   
2      3  1971                               Blue       Joni Mitchell   
3      4  1976           Songs in the Key of Life       Stevie Wonder   
4      5  1969                         Abbey Road         The Beatles   
..   ...   ...                                ...                 ...   
495  496  1998         ¿Dónde están los ladrones?             Shakira   
496  497  1985  The Indestructible Beat of Soweto     Various Artists   
497  498  1977                            Suicide             Suicide   
498  499  1977                          Ask Rufus  Rufus & Chaka Khan   
499  500  2004                            Funeral         Arcade Fire   

                    Type  Rating  Releases                     Genre  
0                  Album    4.65        38                       r&b  
1                  Album    4.45        47                      rock  
2                  Album    4.45        18                      folk  
3                  Album    4.55        24                      soul  
4                  Album    4.70        54                      rock  
..                   ...     ...       ...                       ...  
495                Album    4.50         4                       pop  
496  Album + Compilation     NaN         3  mbaqanga , south african  
497                Album    4.00        10                      rock  
498                Album     NaN         2                       r&b  
499                Album    4.65        17              rock , indie  

[500 rows x 8 columns]

In [373]:
stone.Album = stone.Album.replace(1999,"1999",regex=True)
stone.Album = stone.Album.replace(21,"21",regex=True)
stone.Album = stone.Album.replace(1989,"1989",regex=True)

In [374]:
stone.Artist = stone.Artist.str.strip()
stone.Album = stone.Album.str.strip()
stone.Type = stone.Type.str.strip()
stone.Genre = stone.Genre.str.strip()

In [375]:
stone["Gen"] = stone["Genre"].str.extract(r"(^([^,])+)")[0]
stone["Subgenre"] = stone["Genre"].str.extract(r",\s*(.*$)")[0]

In [376]:
apikey = os.getenv("apikey") #apikey de lastfm

In [377]:
stone.Album = stone.Album.str.replace(r'(Metallica...The Black Album..)',"Metallica",regex=True)
stone.Album = stone.Album.str.replace(r'(Eagles...st album.)',"Eagles",regex=True)
stone.Artist = stone.Artist.str.replace("Neil Young with Crazy Horse","Neil Young & Crazy Horse",regex=True)
stone.Artist = stone.Artist.str.replace(r"(Bob Dylan...The Band)","Bob Dylan And The Band",regex=True)
stone.Artist = stone.Artist.str.replace("Prince and The Revolution","Prince & The Revolution",regex=True)
stone.Artist = stone.Artist.str.replace(r"(Rufus...Chaka Khan)","Rufus",regex=True)
stone.Album = stone.Album.str.replace(r'(Proud Mary.*)',"Proud Mary",regex=True)

In [378]:
stone["Alb_url"] = stone["Album"]
stone["Art_url"] = stone["Artist"]

In [379]:
stone.Alb_url = stone.Alb_url.str.replace(r'(^The Beatles\s..The White Album..)',"The Beatles (Remastered)",regex=True)
stone.Alb_url = stone.Alb_url.str.replace(r'(^The Band...The Brown Album..)',"The Band",regex=True)
#The Band (“The Brown Album”)

In [380]:
stone["Alb_url"] = stone["Alb_url"].str.replace("'","%27",regex=True)
stone["Alb_url"] = stone["Alb_url"].str.replace("&","%26",regex=True)
stone["Alb_url"] = stone["Alb_url"].str.replace(".","%2e",regex=True)
stone["Alb_url"] = stone["Alb_url"].str.replace("/","%2f",regex=True)
stone["Alb_url"] = stone["Alb_url"].str.replace("#","%23",regex=True)
stone["Alb_url"] = stone["Alb_url"].str.replace(r"(\s+)","%20",regex=True)

stone["Art_url"] = stone["Art_url"].str.replace("'","%27",regex=True)
stone["Art_url"] = stone["Art_url"].str.replace("&","%26",regex=True)
stone["Art_url"] = stone["Art_url"].str.replace(".","%2e",regex=True)
stone["Art_url"] = stone["Art_url"].str.replace("/","%2f",regex=True)
stone["Art_url"] = stone["Art_url"].str.replace("#","%23",regex=True)
stone["Art_url"] = stone["Art_url"].str.replace(r"(\s+)","%20",regex=True)

In [311]:
stone.Album = stone.Album.str.replace("_","-",regex=True)
stone.Album = stone.Album.fillna("1999")
stone.Album = stone.Album.str.replace("Ê"," ",regex=True)
stone.Artist = stone.Artist.str.replace("Ê"," ",regex=True)
stone.Genre = stone.Genre.str.replace("Ê"," ",regex=True)
stone.Subgenre = stone.Subgenre.str.replace("Ê"," ",regex=True)
stone.Album = stone.Album.str.replace(r'(^The Band...The Brown.*)',"The Band",regex=True)
stone.Album = stone.Album.str.replace("The B 52's / Play Loud","The B-52's",regex=True)
stone.Artist = stone.Artist.str.replace("The B 52's","The B-52's",regex=True)
stone.Album = stone.Album.str.replace(r'(^Blues Breakers With Eric \w+.+)',"Blues Breakers",regex=True)
stone.Album = stone.Album.str.replace("Proud Mary: The Best of Ike and Tina Turner","Best Of / Proud Mary",regex=True)
stone.Album = stone.Album.str.replace("Ch‰teau","Chateau",regex=True)
stone.Artist = stone.Artist.str.replace("Jay Z","JAY-Z",regex=True)
stone.Artist = stone.Artist.str.replace("Sleater Kinney","Sleater-Kinney")
stone.Artist = stone.Artist.str.replace("Wu Tang Clan","Wu-Tang Clan")

In [381]:
extracto = []
for s in range(len(stone)):

    apikey = os.getenv("apikey")
    artist = stone.loc[s,'Art_url']
    album = stone.loc[s,'Alb_url']
    extracto.append(f"http://ws.audioscrobbler.com/2.0/?method=album.getinfo&api_key={apikey}&artist={artist}&album={album}&format=json")
    


In [382]:
extracto[36]

'http://ws.audioscrobbler.com/2.0/?method=album.getinfo&api_key=be357a07c598ec6108cb3774434676aa&artist=Dr%2e%20Dre&album=The%20Chronic&format=json'

In [383]:
response_dic = {} 
for e in extracto:
    res = requests.get(e)
    i = extracto.index(e)
    response_dic[i] = str(res)
    if i%50==0 or i== 499:
        print(f"{i} done")

0 done
50 done
100 done
150 done
200 done
250 done
300 done
350 done
400 done
450 done
499 done


In [384]:
res_404 = []
for key,value in response_dic.items():
    if response_dic[key] != "<Response [200]>":
        res_404.append(extracto[key])

In [385]:
res_404

['http://ws.audioscrobbler.com/2.0/?method=album.getinfo&api_key=be357a07c598ec6108cb3774434676aa&artist=The%20Allman%20Brothers%20Band&album=At%20Fillmore%20East&format=json']

In [386]:
key_error = []
for key,value in response_dic.items():
    if response_dic[key] != "<Response [200]>":
        key_error.append(key)

In [387]:
print(key_error)

[104]


In [388]:
key_error
stone.iloc[key_error]

#  Year             Album                    Artist          Type  \
104  105  1971  At Fillmore East  The Allman Brothers Band  Album + Live   

     Rating  Releases        Genre   Gen Subgenre               Alb_url  \
104     4.5        27  rock, blues  rock    blues  At%20Fillmore%20East   

                            Art_url  
104  The%20Allman%20Brothers%20Band

In [95]:
stone[stone["Album"]=="The Velvet Underground & Nico"]

#  Year                          Album                         Artist  \
22  23  1967  The Velvet Underground & Nico  The Velvet Underground & Nico   

     Type  Rating  Releases                Genre    Gen      Subgenre  \
22  Album     4.6        33  rock , experimental  rock   experimental   

                                    Alb_url  \
22  The%20Velvet%20Underground%20%26%20Nico   

                                Art_url  
22  The%20Velvet%20Underground %26 Nico

In [75]:
def urls_llamadas ():
    api_urls = []
    apikey = os.getenv("apikey")
    for s in range(len(stone)):
        artist = stone.loc[s,'Art_url']
        album = stone.loc[s,'Alb_url']
        api_urls.append(f"http://ws.audioscrobbler.com/2.0/?method=album.getinfo&api_key={apikey}&artist={artist}&album={album}&format=json")
    request_dic = [] 
    i = 0
    for a in api_urls:
        res = requests.get(a).json()
        request_dic.append(res["album"])
        print(f"{i} done")
        i+=1
    return request_dic


In [76]:
Top500_last = urls_llamadas()

0 done
1 done
2 done
3 done
4 done
5 done
6 done


KeyError: 'album'

In [152]:
api_urls = []
for s in range(len(stone)):
    artist = stone.loc[s,'Art_url']
    album = stone.loc[s,'Alb_url']
    api_urls.append(f"http://ws.audioscrobbler.com/2.0/?method=album.getinfo&api_key={apikey}&artist={artist}&album={album}&format=json")


In [154]:
Top500_last

[{'artist': 'The Beatles',
  'mbid': '03fc0b41-993e-44ae-aa7b-9e6bdc2aba68',
  'tags': {'tag': [{'url': 'https://www.last.fm/tag/60s', 'name': '60s'},
    {'url': 'https://www.last.fm/tag/classic+rock', 'name': 'classic rock'},
    {'url': 'https://www.last.fm/tag/psychedelic', 'name': 'psychedelic'},
    {'url': 'https://www.last.fm/tag/rock', 'name': 'rock'},
    {'url': 'https://www.last.fm/tag/1967', 'name': '1967'}]},
  'playcount': '25183569',
  'image': [{'size': 'small',
    '#text': 'https://lastfm.freetls.fastly.net/i/u/34s/a4e112b368c5ad405d43f0930617c687.png'},
   {'size': 'medium',
    '#text': 'https://lastfm.freetls.fastly.net/i/u/64s/a4e112b368c5ad405d43f0930617c687.png'},
   {'size': 'large',
    '#text': 'https://lastfm.freetls.fastly.net/i/u/174s/a4e112b368c5ad405d43f0930617c687.png'},
   {'size': 'extralarge',
    '#text': 'https://lastfm.freetls.fastly.net/i/u/300x300/a4e112b368c5ad405d43f0930617c687.png'},
   {'size': 'mega',
    '#text': 'https://lastfm.freetls.f

In [153]:
api_urls[36]

'http://ws.audioscrobbler.com/2.0/?method=album.getinfo&api_key=be357a07c598ec6108cb3774434676aa&artist=Eagles&album=Hotel+California&format=json'

In [ ]:
request_dic = [] 
i = 0
for a in api_urls:
    res = requests.get(a).json()
    request_dic.append(res["album"])
    print(f"{i}done")
    i+=1

In [87]:
api_urls[185]

'http://ws.audioscrobbler.com/2.0/?method=album.getinfo&api_key=be357a07c598ec6108cb3774434676aa&artist=Sly & The Family Stone&album=Fresh&format=json'

In [303]:
stone[stone["Artist"] == "JAY Z"] #The B 52's","The B-52's

Empty DataFrame
Columns: [Album, Number, Year, Artist, Genre, Gen, Subgenre, Alb_url, Art_url]
Index: []

In [81]:
Top500_last

[{'artist': 'The Beatles',
  'mbid': '03fc0b41-993e-44ae-aa7b-9e6bdc2aba68',
  'tags': {'tag': [{'url': 'https://www.last.fm/tag/60s', 'name': '60s'},
    {'url': 'https://www.last.fm/tag/classic+rock', 'name': 'classic rock'},
    {'url': 'https://www.last.fm/tag/psychedelic', 'name': 'psychedelic'},
    {'url': 'https://www.last.fm/tag/rock', 'name': 'rock'},
    {'url': 'https://www.last.fm/tag/1967', 'name': '1967'}]},
  'playcount': '25183569',
  'image': [{'size': 'small',
    '#text': 'https://lastfm.freetls.fastly.net/i/u/34s/a4e112b368c5ad405d43f0930617c687.png'},
   {'size': 'medium',
    '#text': 'https://lastfm.freetls.fastly.net/i/u/64s/a4e112b368c5ad405d43f0930617c687.png'},
   {'size': 'large',
    '#text': 'https://lastfm.freetls.fastly.net/i/u/174s/a4e112b368c5ad405d43f0930617c687.png'},
   {'size': 'extralarge',
    '#text': 'https://lastfm.freetls.fastly.net/i/u/300x300/a4e112b368c5ad405d43f0930617c687.png'},
   {'size': 'mega',
    '#text': 'https://lastfm.freetls.f

In [329]:
Top500_last_df = pd.DataFrame(Top500_last)

In [330]:
Top500_last_df[["playcount","listeners"]]=Top500_last_df[["playcount","listeners"]].astype("int64")

In [331]:
Top500_last_df[["artist","name","playcount","listeners"]].sort_values(by='playcount', ascending=True).head(25)

artist  \
310                                            Various   
277                                            Various   
177                Curtis Mayfield and The Impressions   
446  Stan Getz / Joao Gilberto featuring Antonio Ca...   
122                                         Run D.M.C.   
469                                        L.L. Cool J   
254                                          Metallica   
246                                  The Grateful Dead   
420                                    Various Artists   
244                                    Jerry Lee Lewis   
487                                          Husker Du   
22                      John Lennon / Plastic Ono Band   
413                                        The Go Go's   
462                              Echo And The Bunnymen   
142                        Dr. John, the Night Tripper   
127                               Iggy And The Stooges   
402                                     Lynyrd Skynyrd   
407                                    Sinead O'Connor   
131                                    Various Artists   
215                                         Bo Diddley   
258                                              Janet   
376                                    John Lee Hooker   
111                            The Mamas and The Papas   
387                                    Various Artists   
458                                       The Drifters   

                                                  name  playcount  listeners  
310                         The Sun Records Collection          1          1  
277                   Anthology Of American Folk Music          3          3  
177                           The Anthology: 1961-1977        118         10  
446                                    GETZ / GILBERTO        138         19  
122                                       Raising Hell        165         48  
469                                              Radio        183         41  
254                      Metallica ("The Black Album")        722         20  
246                                          Live/Dead        816         79  
420              The Best Of The Girl Groups, Volume 1        928         73  
244  All Killer No Filler! The Jerry Lee Lewis Anth...       1121         76  
487                                     New Day Rising       1437        142  
22                        John Lennon/Plastic Ono Band       1450         95  
413                                Beauty and the Beat       3738        487  
462                                     Heaven Up Here       3797        450  
142                                          Gris-Gris       5409        491  
127                                          Raw Power       5792        733  
402                (Pronounced 'Leh-'Nerd 'Skin-'Nerd)       6304        278  
407                   I Do Not Want What I Haven't Got       6656       1880  
131  Saturday Night Fever: The Original Movie Sound...       6998        434  
215                         Bo Diddley / Go Bo Diddley       7302       1115  
258                                    The Velvet Rope       7893        377  
376                 The Ultimate Collection: 1948-1990       9360        316  
111              If You Can Believe Your Eyes and Ears      10202       2226  
387                  The Indestructible Beat of Soweto      10677        911  
458                          The Drifters' Golden Hits      11038       1066

In [ ]:
Sly